In [1]:
import os
import logging 
import sys

import xarray as xr
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import geopandas as gpd
import json

# Locals
import oggm
import oggm.cfg as cfg
from oggm import utils, workflow, tasks
from oggm.exceptions import InvalidParamsError
from func_add_mesmer_m import process_mesmer_m_data, gcms_mesmer, quantiles, run_hydro_from_2000_ref_area_2000_hist_w5e5_mesmer_m, scenarios


pd_provide_reg_full_name = gpd.read_file('/home/www/lschuster/provide/provide_glacier_regions/provide_glacier_regions.shp')
pd_provide_reg_full_name.index = pd_provide_reg_full_name.provide_id
provide_reg_full_name_dict = dict(pd_provide_reg_full_name['full_name'])
provide_reg_full_name_dict['P06'] = 'East Asia'



#########################
# you can set this to True to do a test on just 32 glaciers
# the default is to run batches of 500 glaciers
test = True
if test:
    n_glacier=32
else:
    n_glacier = 500 # there are so many experiments, let's rather split it in smaller batches ... 
################################

#preg_num = str(sys.argv[1])
#preg_num = str(sys.argv[1]) #7 # central europe
#end_yr = int(sys.argv[2]) # always write 2100 (we don't have the 2300 data)
#preg_num = str(sys.argv[1])
scenario = 'CurPol'
preg_num = 7 # central europe
end_yr = 2100 # int(sys.argv[2]) # 2100

In [ ]:


#####

if len(preg_num)<10:
    Preg = f'P0{preg_num}'
else:
    Preg = f'P{preg_num}'

region = provide_reg_full_name_dict[Preg].replace(' ', '_')

f = open('/home/www/lschuster/provide/provide_glacier_regions/rgi_ids_per_provide_region.json')
rgis_preg = json.load(f)[Preg]
rgis_preg = list(set(rgis_preg)) # the IDs are not unique ... 
rgis_preg = np.sort(rgis_preg) # make sure that the RGIs are sorted ...
# Initialize OGGM and set up the default run parameters
cfg.initialize(logging_level='ERROR')
rgi_version = '62'

border = 160 
cfg.PARAMS['border'] = border # changed for OGGM v16

# I got a strange KeyError: 'dl_verify_data_cluster.klima.uni-bremen.de' (only for RGI reg 03 and  'gfdl-esm4' 'ssp370')
cfg.PARAMS['dl_verify'] = False 
cfg.PARAMS['continue_on_error'] = True
cfg.PARAMS['use_multiprocessing']=True
cfg.PARAMS['store_model_geometry'] = True
           
# Local working directory (where OGGM will write its output)
WORKING_DIR = os.environ.get('OGGM_WORKDIR', '') # TEST
#WORKING_DIR = '/home/www/lschuster/provide/MESMER-M_projections/runs/test_workdir'
    
if not WORKING_DIR:
    raise RuntimeError('Need a working dir')
utils.mkdir(WORKING_DIR)
cfg.PATHS['working_dir'] = WORKING_DIR

OUTPUT_DIR = os.environ.get('OGGM_OUTDIR', '')  # TEST
#OUTPUT_DIR = '/home/www/lschuster/provide/MESMER-M_projections/runs/test_output'


if not OUTPUT_DIR:
    raise RuntimeError('Need an output dir')
utils.mkdir(OUTPUT_DIR)


OGGM_GLACIER_JOB = os.environ.get('OGGM_GLACIER_JOB', '')

id0 = (int(OGGM_GLACIER_JOB)-1)*n_glacier
id1 = (int(OGGM_GLACIER_JOB))*n_glacier
print(id0,id1)
rgi_ids = rgis_preg[id0:id1]    


# Module logger
log = logging.getLogger(__name__)

log.workflow(f'Starting run for Provide reg {Preg} ({region}): glaciers [{id0}:{id1}]')    


ALL_DIAGS = ['volume', 'volume_bsl', 'volume_bwl',  
             'area', 'length',
             'off_area', 'on_area', 
             'melt_off_glacier', 'melt_on_glacier', 
             'liq_prcp_off_glacier', 'liq_prcp_on_glacier',
             'snowfall_off_glacier', 'snowfall_on_glacier']
# Add debug vars
cfg.PARAMS['store_diagnostic_variables'] = ALL_DIAGS
###########################

# Go - get the pre-processed glacier directories
base_url = 'https://cluster.klima.uni-bremen.de/~oggm/gdirs/oggm_v1.6/L3-L5_files/2023.3/elev_bands/W5E5_spinup'
gdirs = workflow.init_glacier_directories(rgi_ids, from_prepro_level=5, prepro_border=border,
                                          prepro_base_url=base_url, prepro_rgi_version=rgi_version)


# directory of mesmer gcm data:
fp_dir = '/home/www/lschuster/provide/MESMER-M_projections/88.198.17.222/mesmer-m-processed/mesmer-m-processed'
year_range=('2000', '2019')
# for some, we don't have yet the data, but it does not matter, because it runs anyways ... 
for scenario in scenarios:
    for model in gcms_mesmer:
        fpath_temp = f'{fp_dir}/{model}/glacier_modellers/{model}_{region}_tas_mon_{scenario}_g025.nc'
        fpath_precip = f'{fp_dir}/{model}/glacier_modellers/{model}_{region}_pr_mon_{scenario}_g025.nc'

        for q in quantiles:
            rid = f'_{scenario}_{model}_q{q}'
            workflow.execute_entity_task(process_mesmer_m_data, gdirs, 
                                        filesuffix=rid+'_bc_2000_2019',
                                        fpath_temp=fpath_temp,
                                        fpath_precip=fpath_precip, y0=2000-10, y1=end_yr+10,
                                        quantile= q, # we need that as additional argument ... 
                                        year_range=year_range # for the bias correction 
                                        )

# it runs it for all scenario, quantiles and gcms ...     
workflow.execute_entity_task(run_hydro_from_2000_ref_area_2000_hist_w5e5_mesmer_m, gdirs, end_yr=end_yr)

# compile and store run output
eq_dir = os.path.join(OUTPUT_DIR, 'oggm_v16/2023.3', str(end_yr), Preg)
utils.mkdir(eq_dir)


for scenario in scenarios:
    for model in gcms_mesmer:
        for q in quantiles:
            rid = f'_{scenario}_{model}_q{q}'
            try:
                utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019', 
                                        path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged{rid}_bc_2000_2019_Batch_{id0}_{id1}.nc'))
            except:
                log.workflow(f'no gcm input data for: {rid}???')


log.workflow('OGGM Done')



In [ ]:
# todo
# to adapt ...
# Example "shape"
# sbatch --array=1-4 run_slurm_with_hydro_per_rgi_reg.slurm 11 2100
from oggm import utils
import numpy as np
import pandas as pd
# get the dataset where coordinates of glaciers are stored
frgi = utils.file_downloader('https://cluster.klima.uni-bremen.de/~oggm/rgi/rgi62_stats.h5')
#frgi = '/home/users/lschuster/glacierMIP/rgi62_stats.h5'
odf = pd.read_hdf(frgi, index_col=0)
n_glac_per_batch = 1000

CMIP = 'CMIP6'
for end_yr in [2100, 2300]:
    for rgi_reg in odf['O1Region'].unique():
        n_batches = int(np.ceil(len(odf.loc[odf.O1Region == rgi_reg])/n_glac_per_batch))
        print(f'sbatch --array=1-{n_batches} run_slurm_with_hydro_per_rgi_reg_2023.3.slurm {rgi_reg} {end_yr} {CMIP}')
    print('\n')
    
CMIP = 'CMIP5'
for end_yr in [2100, 2300]:
    for rgi_reg in odf['O1Region'].unique():
        n_batches = int(np.ceil(len(odf.loc[odf.O1Region == rgi_reg])/n_glac_per_batch))
        print(f'sbatch --array=1-{n_batches} run_slurm_with_hydro_per_rgi_reg_2023.3.slurm {rgi_reg} {end_yr} {CMIP}')
    print('\n')

sbatch --array=1-4 run_slurm_with_hydro_per_provide_reg_mesmer.slurm 7 2100

sbatch --array=1-9 run_slurm_with_hydro_per_provide_reg_mesmer.slurm 4 2100

In [1]:
#preg_num = str(sys.argv[1])
scenario = 'CurPol'
preg_num = 7 # central europe
end_yr = 2100 # int(sys.argv[2]) # 2100


In [36]:
sbatch run_slurm_with_hydro_per_provide_reg_mesmer.slurm 7 'CurPol' 2100


SyntaxError: invalid syntax (1226016489.py, line 1)

In [27]:
f = open('/home/www/lschuster/provide/provide_glacier_regions/rgi_ids_per_provide_region.json')
rgis_preg = json.load(f)['P07']
rgis_preg = list(set(rgis_preg))

In [26]:
len(rgis_preg)

4033

In [4]:
pd_provide_reg_full_name

full_name provide_id  \
provide_id                                                      
P10                                 Northern Andes        P10   
P01                         Western Canada and USA        P01   
P07                                 Central Europe        P07   
P08                       Caucasus and Middle East        P08   
P09                                   Central Asia        P09   
P04                        Scandinavia and Iceland        P04   
P11                                 Southern Andes        P11   
P12                                    New Zealand        P12   
P06                                      East Asia        P06   
P06                                      East Asia        P06   
P05         Svalbard, Jan Mayen and Russian Arctic        P05   
P03                            Greenland Periphery        P03   
P02                                  Arctic Canada        P02   
P13             Subantarctic and Antarctic Islands        P13   

                                                     geometry  
provide_id                                                     
P10         POLYGON ((-100.00000 20.00000, -99.00000 20.00...  
P01         POLYGON ((-89.00000 74.00000, -89.00000 73.000...  
P07         POLYGON ((-6.00000 40.00000, -6.00000 41.00000...  
P08         POLYGON ((32.00000 30.00000, 32.00000 31.00000...  
P09         POLYGON ((57.00000 70.00000, 58.00000 70.00000...  
P04         POLYGON ((35.00000 74.00000, 35.00000 73.00000...  
P11         POLYGON ((-82.00000 -57.00000, -82.00000 -56.0...  
P12         POLYGON ((164.00000 -34.00000, 165.00000 -34.0...  
P06         POLYGON ((-169.00000 78.00000, -169.00000 77.0...  
P06         POLYGON ((128.00000 31.00000, 128.00000 32.000...  
P05         POLYGON ((128.00000 70.00000, 127.00000 70.000...  
P03         POLYGON ((-75.00000 77.00000, -74.73000 77.510...  
P02         POLYGON ((-125.00000 74.00000, -125.00000 75.0...  
P13         POLYGON ((-180.00000 -45.00000, -179.00000 -45...

In [3]:
import os
import logging 
import sys

import xarray as xr
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import geopandas as gpd
import json

# Locals
import oggm
import oggm.cfg as cfg
from oggm import utils, workflow, tasks
from oggm.exceptions import InvalidParamsError
from func_add_mesmer_m import process_mesmer_m_data, gcms_mesmer, quantiles, run_hydro_from_2000_ref_area_2000_hist_w5e5_mesmer_m


pd_provide_reg_full_name = gpd.read_file('/home/www/lschuster/provide/provide_glacier_regions/provide_glacier_regions.shp')
pd_provide_reg_full_name.index = pd_provide_reg_full_name.provide_id
provide_reg_full_name_dict = dict(pd_provide_reg_full_name['full_name'])
provide_reg_full_name_dict['P06'] = 'East Asia'

if preg_num<10:
    Preg = f'P0{preg_num}'
else:
    Preg = f'P{preg_num}'

region = provide_reg_full_name_dict[Preg].replace(' ', '_')

f = open('/home/www/lschuster/provide/provide_glacier_regions/rgi_ids_per_provide_region.json')
rgis_preg = json.load(f)[Preg]

#########################
# you can set this to True to do a test on just 32 glaciers
# the default is to run batches of 1000 glaciers
test = True
if test:
    n_glacier=32
else:
    n_glacier = 1000
################################

NameError: name 'preg_num' is not defined

In [8]:
# Initialize OGGM and set up the default run parameters
cfg.initialize(logging_level='ERROR')
rgi_version = '62'

cfg.PARAMS['border'] = 240 # changed for OGGM v16

# I got a strange KeyError: 'dl_verify_data_cluster.klima.uni-bremen.de' (only for RGI reg 03 and  'gfdl-esm4' 'ssp370')
cfg.PARAMS['dl_verify'] = False 
cfg.PARAMS['continue_on_error'] = True
cfg.PARAMS['use_multiprocessing']=True
cfg.PARAMS['store_model_geometry'] = True
           
# Local working directory (where OGGM will write its output)
WORKING_DIR = os.environ.get('OGGM_WORKDIR', '') # TEST
WORKING_DIR = '/home/www/lschuster/provide/MESMER-M_projections/runs/test_workdir'
    
if not WORKING_DIR:
    raise RuntimeError('Need a working dir')
utils.mkdir(WORKING_DIR)
cfg.PATHS['working_dir'] = WORKING_DIR

OUTPUT_DIR = os.environ.get('OGGM_OUTDIR', '')  # TEST
OUTPUT_DIR = '/home/www/lschuster/provide/MESMER-M_projections/runs/test_output'


if not OUTPUT_DIR:
    raise RuntimeError('Need an output dir')
utils.mkdir(OUTPUT_DIR)


OGGM_GLACIER_JOB = os.environ.get('OGGM_GLACIER_JOB', '')
OGGM_GLACIER_JOB = 1 

id0 = (int(OGGM_GLACIER_JOB)-1)*n_glacier
id1 = (int(OGGM_GLACIER_JOB))*n_glacier
print(id0,id1)

rgi_ids = rgis_preg[id0:id1]    

#if rgi_reg not in ['{:02d}'.format(r) for r in range(1, 20)]:
#    raise RuntimeError('Need an RGI Region')

#gcm = str(sys.argv[1])
#ssp = str(sys.argv[2])

# Module logger
log = logging.getLogger(__name__)
log.workflow(f'Starting run for Provide reg {Preg} ({region}): glaciers [{id0}:{id1}] using scenario {scenario}')    


ALL_DIAGS = ['volume', 'volume_bsl', 'volume_bwl',  # added that again as this should be repaired after PR #todo-> need to add that again 
             'area', 'length',  'calving', 'calving_rate',
             'off_area', 'on_area', 'melt_off_glacier',
             'melt_on_glacier', 'liq_prcp_off_glacier', 'liq_prcp_on_glacier',
             'snowfall_off_glacier', 'snowfall_on_glacier', 'model_mb',
             'residual_mb', 'snow_bucket']
# Add debug vars
cfg.PARAMS['store_diagnostic_variables'] = ALL_DIAGS

2023-09-29 17:07:09: oggm.cfg: Reading default parameters from the OGGM `params.cfg` configuration file.
2023-09-29 17:07:09: oggm.cfg: Multiprocessing switched OFF according to the parameter file.
2023-09-29 17:07:09: oggm.cfg: Multiprocessing: using all available processors (N=32)
2023-09-29 17:07:09: oggm.cfg: PARAMS['border'] changed from `80` to `240`.
2023-09-29 17:07:09: oggm.cfg: PARAMS['continue_on_error'] changed from `False` to `True`.
2023-09-29 17:07:09: oggm.cfg: Multiprocessing switched ON after user settings.
2023-09-29 17:07:09: oggm.cfg: PARAMS['store_model_geometry'] changed from `False` to `True`.
2023-09-29 17:07:09: __main__: Starting run for Provide reg P07 (Central_Europe): glaciers [0:32] using scenario CurPol
2023-09-29 17:07:09: oggm.cfg: PARAMS['store_diagnostic_variables'] changed from `['volume', 'volume_bsl', 'volume_bwl', 'area', 'length', 'calving', 'calving_rate', 'off_area', 'on_area', 'melt_off_glacier', 'melt_on_glacier', 'liq_prcp_off_glacier', 'li

0 32


In [10]:
load = True
if load:
    # Go - get the pre-processed glacier directories
    base_url = 'https://cluster.klima.uni-bremen.de/~oggm/gdirs/oggm_v1.6/L3-L5_files/2023.3/elev_bands/W5E5_spinup'
    gdirs = workflow.init_glacier_directories(rgi_ids, from_prepro_level=5, prepro_border=160,
                                              prepro_base_url=base_url, prepro_rgi_version=rgi_version)
    
    fp_dir = '/home/www/lschuster/provide/MESMER-M_projections/88.198.17.222/mesmer-m-processed/mesmer-m-processed'
    year_range=('2000', '2019')

    # for some, we don't have yet the data, but it does not matter, because it runs anyways ... 
    for model in gcms_mesmer:
        fpath_temp = f'{fp_dir}/{model}/glacier_modellers/{model}_{region}_tas_mon_{scenario}_g025.nc'
        fpath_precip = f'{fp_dir}/{model}/glacier_modellers/{model}_{region}_pr_mon_{scenario}_g025.nc'

        for q in quantiles:
            rid = f'_{scenario}_{model}_q{q}'
            workflow.execute_entity_task(process_mesmer_m_data, gdirs, 
                                        filesuffix=rid+'_bc_2000_2019',
                                        fpath_temp=fpath_temp,
                                        fpath_precip=fpath_precip, y0=2000-10, y1=end_yr+10,
                                        quantile= q, # we need that as additional argument ... 
                                        year_range=year_range # for the bias correction 
                                        )
            
else:
    gdirs = workflow.init_glacier_directories(rgi_ids)

2023-09-29 17:08:09: oggm.workflow: init_glacier_directories from prepro level 5 on 32 glaciers.
2023-09-29 17:08:09: oggm.workflow: Execute entity tasks [gdir_from_prepro] on 32 glaciers
2023-09-29 17:08:10: oggm.workflow: Execute entity tasks [process_mesmer_m_data] on 32 glaciers
2023-09-29 17:08:10: oggm.workflow: Execute entity tasks [process_mesmer_m_data] on 32 glaciers
2023-09-29 17:08:11: oggm.workflow: Execute entity tasks [process_mesmer_m_data] on 32 glaciers
2023-09-29 17:08:11: oggm.workflow: Execute entity tasks [process_mesmer_m_data] on 32 glaciers
2023-09-29 17:08:11: oggm.workflow: Execute entity tasks [process_mesmer_m_data] on 32 glaciers
2023-09-29 17:08:11: oggm.workflow: Execute entity tasks [process_mesmer_m_data] on 32 glaciers
2023-09-29 17:08:14: oggm.workflow: Execute entity tasks [process_mesmer_m_data] on 32 glaciers
2023-09-29 17:08:18: oggm.workflow: Execute entity tasks [process_mesmer_m_data] on 32 glaciers
2023-09-29 17:08:21: oggm.workflow: Execute 

In [35]:
eq_dir = os.path.join(OUTPUT_DIR, 'oggm_v16/2023.3', str(end_yr), Preg)
utils.mkdir(eq_dir)


'/home/www/lschuster/provide/MESMER-M_projections/runs/test_output/oggm_v16/2023.3/2100/P07'

In [20]:
workflow.execute_entity_task(run_hydro_from_2000_ref_area_2000_hist_w5e5_mesmer_m, gdirs, end_yr=end_yr, scenario = scenario)

# compile and store run output
eq_dir = os.path.join(OUTPUT_DIR, str(end_yr), Preg)
utils.mkdir(eq_dir)

for model in gcms_mesmer:
    for q in quantiles:
        rid = f'_{scenario}_{model}_q{q}'
        try:
            utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019', 
                                    path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged{rid}_bc_2000_2019_Batch_{id0}_{id1}.nc'))
        except:
            log.workflow(f'no gcm input data for: {rid}???')


log.workflow('OGGM Done')



2023-09-29 17:15:13: oggm.workflow: Execute entity tasks [run_hydro_from_2000_ref_area_2000_hist_w5e5_mesmer_m] on 32 glaciers


[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None]

### other script parts that are not necessary 

In [14]:
# SCRIPT to run the CMIP5, CMIP6 and ISIMIP3b_CMIP6 projections until 2100 or until 2300
# using OGGM v1.6.1
########################################################################################
import os
import logging 
import sys

# Libs
import xarray as xr
import pandas as pd
import numpy as np
import geopandas as gpd
import matplotlib.pyplot as plt

# Locals
import oggm.cfg as cfg
from oggm import utils, workflow, tasks
from oggm.exceptions import InvalidParamsError
from oggm.shop.gcm_climate import process_monthly_isimip_data, process_cmip_data

# we created some helper functions which are in func_add.py
from func_add import run_hydro_from_2000_ref_area_2000_hist_gcm, run_hydro_from_2000_ref_area_2000_hist_w5e5


# preprocess climate files 
if end_yr == 2100 and CMIP_version=='CMIP6':
    # we compute both ISIMIP3b_CMIP6 and CMIP6 in one run

    # preprocess ISIMIP3b_CMIP6
    # 'gfdl-esm4_r1i1p1f1', 'mpi-esm1-2-hr_r1i1p1f1', 'mri-esm2-0_r1i1p1f1' ("low sensitivity" models, within typical ranges from AR6)
    # 'ipsl-cm6a-lr_r1i1p1f1', 'ukesm1-0-ll_r1i1p1f2' ("hotter" models, especially ukesm1-0-ll)
    isimip3b_members = ['gfdl-esm4_r1i1p1f1', 'mpi-esm1-2-hr_r1i1p1f1', 'mri-esm2-0_r1i1p1f1',
                        'ipsl-cm6a-lr_r1i1p1f1', 'ukesm1-0-ll_r1i1p1f2' ]
    for member in isimip3b_members:
        # Download the three main SSPs
        for ssp in ['ssp126', 'ssp370','ssp585']:
            # bias correct them
            rid = f'_ISIMIP3b_{member}_{ssp}'
            workflow.execute_entity_task(process_monthly_isimip_data, gdirs, 
                                         ssp = ssp,
                                         # gcm member -> you can choose another one
                                         member=member,
                                         # recognize the climate file for later
                                         output_filesuffix=rid,
                                         y0=2000, # no additional bias correction anyways ...
                                         );
            if bc_isimip_2000_2019:
                workflow.execute_entity_task(process_monthly_isimip_data, gdirs, 
                                 ssp = ssp,
                                 # gcm member -> you can choose another one
                                 member=member,
                                             year_range=('2000', '2019'),
                                             apply_bias_correction=True,
                                             y0=2000-10,
                                 # recognize the climate file for later
                                 output_filesuffix=rid+'_bc_2000_2019'
                                 );

    # preprocess CMIP6
    gcms_cmip6 = pd.read_csv('/home/www/oggm/cmip6/all_gcm_list.csv', index_col=0)
    # take all gcms 
    for gcm in gcms_cmip6.gcm.unique(): ##TEST:
        df1 = gcms_cmip6.loc[gcms_cmip6.gcm == gcm]
        for ssp in df1.ssp.unique():
            df2 = df1.loc[df1.ssp == ssp]
            assert len(df2) == 2
            ft = df2.loc[df2['var'] == 'tas'].iloc[0]
            fp = df2.loc[df2['var'] == 'pr'].iloc[0].path
            rid = ft.fname.replace('_r1i1p1f1_tas.nc', '')
            rid='_CMIP6_' + rid
            ft = ft.path

            workflow.execute_entity_task(process_cmip_data, gdirs, 
                                         filesuffix=rid+'_bc_2000_2019',  # recognize the climate file for later
                                         fpath_temp=ft,  # temperature projections
                                         fpath_precip=fp,  # precip projections
                                         year_range=('2000', '2019'),
                                         y0=2000-10,y1=2100+10,
                                         );
            if bc_comparison_1979_2014:
                # only do that for comparison for the common ssps with isimip3b
                if gcm.lower() in ['gfdl-esm4', 'mpi-esm1-2-hr', 'mri-esm2-0']: 
                    if ssp in ['ssp126', 'ssp370', 'ssp585']:
                        workflow.execute_entity_task(process_cmip_data, gdirs, 
                                                 filesuffix=rid+'_bc_1979_2014',  # recognize the climate file for later
                                                 fpath_temp=ft,  # temperature projections
                                                 fpath_precip=fp,  # precip projections
                                                 year_range=('1979', '2014'),
                                                 y0=1979-18,y1=2100+18,
                                                 );
            
elif end_yr == 2300 and CMIP_version=='CMIP6':
    # normally do that here, but cluster has not the right pandas version to do pd.read_html...
    #gcms_cmip6 = pd.read_csv('/home/www/oggm/cmip6/all_gcm_list.csv', index_col='index')
    #pd_t = pd.read_html('/home/www/oggm/cmip6/all_gcm_table.html')[0]
    #folder_p = '/home/www/oggm/cmip6/GCM/'
    #pd_t = pd_t.loc[pd_t.y1>=2299]
    #pd_t['path'] = folder_p + pd_t['folder'] + '/' + pd_t['fname'] 
    # now we select those from the total list 
    #gcms_cmip6.index = gcms_cmip6.path
    #gcms_cmip6= gcms_cmip6.loc[pd_t.path] 
    #gcms_cmip6 = gcms_cmip6.reset_index(drop=True)
    #gcms_cmip6 = gcms_cmip6.drop(columns=['Unnamed: 0'])
    #gcms_cmip6.to_csv('/home/www/oggm/oggm-standard-projections/oggm_v16/2023.3/_run_scripts/all_gcm_list_2300.csv')
    gcms_cmip6 = pd.read_csv('/home/www/oggm/oggm-standard-projections/oggm_v16/2023.3/_run_scripts/all_gcm_list_2300.csv', index_col= 'Unnamed: 0')
    
    # only take those gcms that go until 2300
    for gcm in gcms_cmip6.gcm.unique():
        df1 = gcms_cmip6.loc[gcms_cmip6.gcm == gcm]
        for ssp in df1.ssp.unique():
            df2 = df1.loc[df1.ssp == ssp]
            assert len(df2) == 2
            ft = df2.loc[df2['var'] == 'tas'].iloc[0]
            fp = df2.loc[df2['var'] == 'pr'].iloc[0].path
            rid = ft.fname.replace('_r1i1p1f1_tas.nc', '')
            rid='_CMIP6_' + rid
            ft = ft.path

            workflow.execute_entity_task(process_cmip_data, gdirs, 
                                         filesuffix=rid+'_bc_2000_2019',  # recognize the climate file for later
                                         fpath_temp=ft,  # temperature projections
                                         fpath_precip=fp,  # precip projections
                                         year_range=('2000', '2019'),
                                         y0=2000-10,
                                         );


elif end_yr == 2100  and CMIP_version=='CMIP5':
    gcms_cmip5 = pd.read_csv('/home/www/oggm/cmip5-ng/all_gcm_list.csv', index_col=0)
    # just to repeat the CMIP
    gcms_cmip5 = pd.read_csv('/home/www/oggm/oggm-standard-projections/oggm_v16/2023.3/_run_scripts/all_gcm_list_2300_cmip5_vAug2023.csv',
                             index_col=0)
    gcms_cmip5 = gcms_cmip5.loc[gcms_cmip5.gcm == 'CESM1-CAM5']
    for gcm in gcms_cmip5.gcm.unique(): 
        df1 = gcms_cmip5.loc[gcms_cmip5.gcm == gcm]
        df1 = df1.loc[df1.rcp!='historicalGHG']
        df1 = df1.loc[df1.rcp!='historicalNat']
        for rcp in df1.rcp.unique():
            df2 = df1.loc[df1.rcp == rcp]
            assert len(df2) == 2
            ft = df2.loc[df2['var'] == 'tas'].iloc[0]
            fp = df2.loc[df2['var'] == 'pr'].iloc[0].path

            # don'need the realisation, as it is the same _r1i1p1_g025
            rid = ft.fname.replace('_r1i1p1_g025.nc', '')
            rid='_CMIP5_' + rid
            rid = rid.replace('_tas_mon', '')
            
            ft = ft.path
            workflow.execute_entity_task(process_cmip_data, gdirs, 
                                         filesuffix=rid+'_bc_2000_2019',  # recognize the climate file for later
                                         fpath_temp=ft,  # temperature projections
                                         fpath_precip=fp,  # precip projections
                                         year_range=('2000', '2019'),
                                         y0=2000-10,
                                         );
elif end_yr == 2300  and CMIP_version=='CMIP5':
    gcms_cmip5 = pd.read_csv('/home/www/oggm/oggm-standard-projections/oggm_v16/2023.3/_run_scripts/all_gcm_list_2300_cmip5_vAug2023.csv',
                             index_col=0)
    for gcm in gcms_cmip5.gcm.unique(): 
        df1 = gcms_cmip5.loc[gcms_cmip5.gcm == gcm]
        df1 = df1.loc[df1.rcp!='historicalGHG']
        df1 = df1.loc[df1.rcp!='historicalNat']
        for rcp in df1.rcp.unique():
            df2 = df1.loc[df1.rcp == rcp]
            assert len(df2) == 2
            ft = df2.loc[df2['var'] == 'tas'].iloc[0]
            fp = df2.loc[df2['var'] == 'pr'].iloc[0].path

            # don'need the realisation, as it is the same _r1i1p1
            rid = ft.fname.replace('_r1i1p1.nc', '')
            rid='_CMIP5_' + rid
            rid = rid.replace('_tas_mon', '')
            
            ft = ft.path
            workflow.execute_entity_task(process_cmip_data, gdirs, 
                                         filesuffix=rid+'_bc_2000_2019',  # recognize the climate file for later
                                         fpath_temp=ft,  # temperature projections
                                         fpath_precip=fp,  # precip projections
                                         year_range=('2000', '2019'),
                                         y0=2000-10,
                                         );
    
else:
    raise InvalidParamsError('Wrong end_yr and CMIP version combination!!!')
            
            
# Now comes the actual run
# first using gcm from 2000-end_yr (this is how it is done in Rounce et al., 2023): -> creates:  `gcm_from_2000`
workflow.execute_entity_task(run_hydro_from_2000_ref_area_2000_hist_gcm, gdirs, end_yr = end_yr, bc_isimip_2000_2019=bc_isimip_2000_2019, bc_comparison_1979_2014=bc_comparison_1979_2014,
                            CMIP_version=CMIP_version)
# then using W5E5 from 2000-2019, and GCM from 2020-end_yr (this is how it has normally been done in OGGM): -> creates: `w5e5_gcm_merged`
workflow.execute_entity_task(run_hydro_from_2000_ref_area_2000_hist_w5e5, gdirs, end_yr = end_yr, bc_isimip_2000_2019=bc_isimip_2000_2019, bc_comparison_1979_2014=bc_comparison_1979_2014,
                            CMIP_version=CMIP_version)


# compile and store run output
eq_dir = os.path.join(OUTPUT_DIR, 'RGI' + rgi_reg)
utils.mkdir(eq_dir)

# merge data together
if end_yr == 2100 and CMIP_version=='CMIP6':
    # ISIMIP3b_CMIP6 only goes until 2100
    for member in isimip3b_members:    
        for ssp in ['ssp126', 'ssp370', 'ssp585']:
            rid = f'_ISIMIP3b_{member}_{ssp}'
            # for W5E5 as past climate 
            utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}', 
                            path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged_endyr2100{rid}_rgi{rgi_reg}_{id0}_{id1}.nc'))
            # for the GCM as past climate 
            utils.compile_run_output(gdirs, input_filesuffix=f'_gcm_from_2000_run{rid}', 
                            path=os.path.join(eq_dir, f'run_hydro_gcm_from_2000_endyr2100{rid}_rgi{rgi_reg}_{id0}_{id1}.nc'))
            
            if bc_isimip_2000_2019:
                utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}_bc_2000_2019', 
                            path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged_endyr2100{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))
                utils.compile_run_output(gdirs, input_filesuffix=f'_gcm_from_2000_run{rid}_bc_2000_2019', 
                                path=os.path.join(eq_dir, f'run_hydro_gcm_from_2000_endyr2100{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))

if CMIP_version=='CMIP6':
    for gcm in gcms_cmip6.gcm.unique(): 
        df1 = gcms_cmip6.loc[gcms_cmip6.gcm == gcm]
        for ssp in df1.ssp.unique():
            df2 = df1.loc[df1.ssp == ssp]
            assert len(df2) == 2
            ft = df2.loc[df2['var'] == 'tas'].iloc[0]
            rid = ft.fname.replace('_r1i1p1f1_tas.nc', '')
            rid='_CMIP6_' + rid

            utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019', 
                                    path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged_endyr{end_yr}{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))

            utils.compile_run_output(gdirs, input_filesuffix=f'_gcm_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019', 
                                    path=os.path.join(eq_dir, f'run_hydro_gcm_from_2000_endyr{end_yr}{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))

            if (end_yr == 2100) and (bc_comparison_1979_2014):
                # only do that for comparison for the common ssps with isimip3b
                if gcm.lower() in ['gfdl-esm4', 'mpi-esm1-2-hr', 'mri-esm2-0']: 
                    if ssp in ['ssp126', 'ssp370', 'ssp585']:
                        utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}_endyr{end_yr}_bc_1979_2014', 
                                                path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged_endyr{end_yr}{rid}_bc_1979_2014_rgi{rgi_reg}_{id0}_{id1}.nc'))

                        utils.compile_run_output(gdirs, input_filesuffix=f'_gcm_from_2000_run{rid}_endyr{end_yr}_bc_1979_2014', 
                                                path=os.path.join(eq_dir, f'run_hydro_gcm_from_2000_endyr{end_yr}{rid}_bc_1979_2014_rgi{rgi_reg}_{id0}_{id1}.nc'))

elif CMIP_version=='CMIP5':
    for gcm in gcms_cmip5.gcm.unique(): 
        df1 = gcms_cmip5.loc[gcms_cmip5.gcm == gcm]
        df1 = df1.loc[df1.rcp!='historicalGHG']
        df1 = df1.loc[df1.rcp!='historicalNat']
        for rcp in df1.rcp.unique():
            df2 = df1.loc[df1.rcp == rcp]
            assert len(df2) == 2
            ft = df2.loc[df2['var'] == 'tas'].iloc[0]
            # don'need the realisation, as it is the same _r1i1p1_g025
            if end_yr==2100:
                rid = ft.fname.replace('_r1i1p1_g025.nc', '')
            elif end_yr==2300:
                rid = ft.fname.replace('_r1i1p1.nc', '')
            rid='_CMIP5_' + rid
            rid = rid.replace('_tas_mon', '')
            
            utils.compile_run_output(gdirs, input_filesuffix=f'_merged_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019', 
                                    path=os.path.join(eq_dir, f'run_hydro_w5e5_gcm_merged_endyr{end_yr}{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))

            utils.compile_run_output(gdirs, input_filesuffix=f'_gcm_from_2000_run{rid}_endyr{end_yr}_bc_2000_2019', 
                                    path=os.path.join(eq_dir, f'run_hydro_gcm_from_2000_endyr{end_yr}{rid}_bc_2000_2019_rgi{rgi_reg}_{id0}_{id1}.nc'))
    

log.workflow('OGGM Done')

# Note that the format is a bit different to the ones in https://cluster.klima.uni-bremen.de/~oggm/oggm-standard-projections/oggm_v16/2023.3/,
# as we did some restructuring and renaming afterwards -> see `move_files_in_oggm_folder.ipynb`. 

['RGI60-19.00001',
 'RGI60-19.00002',
 'RGI60-19.00003',
 'RGI60-19.00004',
 'RGI60-19.00005',
 'RGI60-19.00006',
 'RGI60-19.00007',
 'RGI60-19.00008',
 'RGI60-19.00009',
 'RGI60-19.00010',
 'RGI60-19.00011',
 'RGI60-19.00012',
 'RGI60-19.00013',
 'RGI60-19.00014',
 'RGI60-19.00015',
 'RGI60-19.00016',
 'RGI60-19.00017',
 'RGI60-19.00018',
 'RGI60-19.00019',
 'RGI60-19.00020',
 'RGI60-19.00021',
 'RGI60-19.00022',
 'RGI60-19.00023',
 'RGI60-19.00024',
 'RGI60-19.00025',
 'RGI60-19.00026',
 'RGI60-19.00027',
 'RGI60-19.00028',
 'RGI60-19.00029',
 'RGI60-19.00030',
 'RGI60-19.00031',
 'RGI60-19.00032',
 'RGI60-19.00033',
 'RGI60-19.00034',
 'RGI60-19.00035',
 'RGI60-19.00036',
 'RGI60-19.00037',
 'RGI60-19.00038',
 'RGI60-19.00039',
 'RGI60-19.00040',
 'RGI60-19.00041',
 'RGI60-19.00042',
 'RGI60-19.00043',
 'RGI60-19.00044',
 'RGI60-19.00045',
 'RGI60-19.00046',
 'RGI60-19.00047',
 'RGI60-19.00048',
 'RGI60-19.00049',
 'RGI60-19.00050',
 'RGI60-19.00051',
 'RGI60-19.00052',
 'RGI60-19.0